# Setup

## Install addition packages

In [1]:
import os

# The Google Cloud Notebook product has specific requirements
IS_GOOGLE_CLOUD_NOTEBOOK = os.path.exists("/opt/deeplearning/metadata/env_version")

# Google Cloud Notebook requires dependencies to be installed with '--user'
USER_FLAG = ""
if IS_GOOGLE_CLOUD_NOTEBOOK:
    USER_FLAG = "--user"

In [2]:
%%capture
!pip -q install {USER_FLAG} --upgrade transformers
!pip -q install {USER_FLAG} --upgrade datasets
!pip -q install {USER_FLAG} --upgrade tqdm
!pip -q install {USER_FLAG} --upgrade cloudml-hypertune

In [3]:
%%capture
!pip -q install {USER_FLAG} --upgrade google-cloud-aiplatform

In [4]:
# Automatically restart kernel after installs
import os

if not os.getenv("IS_TESTING"):
    # Automatically restart kernel after installs
    import IPython

    app = IPython.Application.instance()
    app.kernel.do_shutdown(True)

In [1]:
%%capture
!pip install git+https://github.com/huggingface/transformers.git datasets pandas torch
!pip install transformers[torch]
!pip install accelerate -U

## Set Project ID

In [2]:
PROJECT_ID = "iKame-gem-ai-research"  # <---CHANGE THIS TO YOUR PROJECT

import os

# Get your Google Cloud project ID using google.auth
if not os.getenv("IS_TESTING"):
    import google.auth

    _, PROJECT_ID = google.auth.default()
    print("Project ID: ", PROJECT_ID)

# validate PROJECT_ID
if PROJECT_ID == "" or PROJECT_ID is None or PROJECT_ID == "iKame-gem-ai-research":
    print(
        f"Please set your project id before proceeding to next step. Currently it's set as {PROJECT_ID}"
    )

Project ID:  ikame-gem-ai-research


In [3]:
from datetime import datetime


def get_timestamp():
    return datetime.now().strftime("%Y%m%d%H%M%S")


TIMESTAMP = get_timestamp()
print(f"TIMESTAMP = {TIMESTAMP}")

TIMESTAMP = 20240108040502


## Create Cloud Storage bucket

In [4]:
BUCKET_NAME = "gs://iKame-gem-ai-research"  # <---CHANGE THIS TO YOUR BUCKET
REGION = "us-central1"  # @param {type:"string"}

In [5]:
if BUCKET_NAME == "" or BUCKET_NAME is None or BUCKET_NAME == "gs://iKame-gem-ai-research":
    BUCKET_NAME = f"gs://{PROJECT_ID}-bucket-review"

In [6]:
print(f"PROJECT_ID = {PROJECT_ID}")
print(f"BUCKET_NAME = {BUCKET_NAME}")
print(f"REGION = {REGION}")

PROJECT_ID = ikame-gem-ai-research
BUCKET_NAME = gs://ikame-gem-ai-research-bucket-review
REGION = us-central1


In [7]:
# ! gsutil mb -l $REGION $BUCKET_NAME

In [8]:
! gsutil ls -al $BUCKET_NAME #validate access to your Cloud Storage bucket

      3078  2024-01-05T01:42:25Z  gs://ikame-gem-ai-research-bucket-review/batch_examples.csv#1704418945853255  metageneration=1
                                 gs://ikame-gem-ai-research-bucket-review/pipeline_root/
TOTAL: 1 objects, 3078 bytes (3.01 KiB)


## Install libraries

In [9]:
import base64
import json
import os
import random
import sys

import google.auth
from google.cloud import aiplatform
from google.cloud.aiplatform import gapic as aip
from google.cloud.aiplatform import hyperparameter_tuning as hpt
from google.protobuf.json_format import MessageToDict

In [10]:
from IPython.display import HTML, display

In [11]:
import datasets
from datasets import Dataset, DatasetDict
import numpy as np
import pandas as pd
import torch
import transformers
from datasets import ClassLabel, Sequence, load_dataset
from transformers import (AutoModelForSequenceClassification, AutoTokenizer,BertForSequenceClassification,
                          EvalPrediction, Trainer, TrainingArguments,PreTrainedModel,BertModel,
                          default_data_collator)

In [12]:
from google.cloud import bigquery
from google.cloud import storage

client = bigquery.Client()
storage_client = storage.Client()

In [13]:
print(f"Notebook runtime: {'GPU' if torch.cuda.is_available() else 'CPU'}")
print(f"PyTorch version : {torch.__version__}")
print(f"Transformers version : {datasets.__version__}")
print(f"Datasets version : {transformers.__version__}")

Notebook runtime: GPU
PyTorch version : 2.0.0+cu118
Transformers version : 2.16.1
Datasets version : 4.37.0.dev0


In [15]:
os.environ["TOKENIZERS_PARALLELISM"] = "false"

In [14]:
APP_NAME = "aift-review-classificatio-multiple-label"

In [ ]:
!cd aift-model-review-multiple-label-classification

# Training

## Preprocess data

In [16]:
model_ckpt = "distilbert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

def tokenize_and_encode(examples):
    return tokenizer(examples["review"], truncation=True)

In [17]:
sql = f"""
SELECT * FROM `ikame-gem-ai-research.AIFT.reviews_multi_label_training`
"""
data = client.query(sql).to_dataframe()
data= data.fillna('0')
for i in data.columns:
    if i != 'review':
        data[i] = data[i].astype(int)

data = Dataset.from_pandas(data).train_test_split(test_size=0.2,shuffle = True, seed=0)
cols = data["train"].column_names
data = data.map(lambda x : {"labels": [x[c] for c in cols if c != "review"]})

# Tokenize and encode
dataset = data.map(tokenize_and_encode, batched=True, remove_columns=cols)

Map:   0%|          | 0/556 [00:00<?, ? examples/s]

Map:   0%|          | 0/140 [00:00<?, ? examples/s]

Map:   0%|          | 0/556 [00:00<?, ? examples/s]

Map:   0%|          | 0/140 [00:00<?, ? examples/s]

In [18]:
labels = [label for label in data['train'].features.keys() if label not in ['review','labels']]
id2label = {idx:label for idx, label in enumerate(labels)}
label2id = {label:idx for idx, label in enumerate(labels)}
labels

['ads', 'bugs', 'positive', 'negative', 'graphic', 'gameplay', 'request']

In [19]:
dataset["train"][0]

{'labels': [0, 1, 0, 0, 0, 1, 0],
 'input_ids': [101,
  8795,
  11100,
  2024,
  10599,
  2030,
  11829,
  5999,
  1010,
  2437,
  14967,
  25198,
  1012,
  102],
 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]}

## Fine-tuning

In [20]:
class BertForMultilabelSequenceClassification(BertForSequenceClassification):
    def __init__(self, config):
      super().__init__(config)

    def forward(self,
        input_ids=None,
        attention_mask=None,
        token_type_ids=None,
        position_ids=None,
        head_mask=None,
        inputs_embeds=None,
        labels=None,
        output_attentions=None,
        output_hidden_states=None,
        return_dict=None):
        return_dict = return_dict if return_dict is not None else self.config.use_return_dict

        outputs = self.bert(input_ids,
            attention_mask=attention_mask,
            token_type_ids=token_type_ids,
            position_ids=position_ids,
            head_mask=head_mask,
            inputs_embeds=inputs_embeds,
            output_attentions=output_attentions,
            output_hidden_states=output_hidden_states,
            return_dict=return_dict)

        pooled_output = outputs[1]
        pooled_output = self.dropout(pooled_output)
        logits = self.classifier(pooled_output)

        loss = None
        if labels is not None:
            loss_fct = torch.nn.BCEWithLogitsLoss()
            loss = loss_fct(logits.view(-1, self.num_labels),
                            labels.float().view(-1, self.num_labels))

        if not return_dict:
            output = (logits,) + outputs[2:]
            return ((loss,) + output) if loss is not None else output

        return SequenceClassifierOutput(loss=loss,
            logits=logits,
            hidden_states=outputs.hidden_states,
            attentions=outputs.attentions)

In [21]:
num_labels=7
model = BertForMultilabelSequenceClassification.from_pretrained(model_ckpt, num_labels=num_labels).to('cuda')

You are using a model of type distilbert to instantiate a model of type bert. This is not supported for all configurations of models and can yield errors.
Some weights of BertForMultilabelSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['encoder.layer.11.attention.self.key.bias', 'encoder.layer.6.attention.output.LayerNorm.bias', 'encoder.layer.3.attention.output.LayerNorm.bias', 'encoder.layer.11.attention.self.query.weight', 'encoder.layer.6.attention.self.value.bias', 'encoder.layer.4.output.LayerNorm.bias', 'encoder.layer.4.attention.self.key.bias', 'encoder.layer.9.output.LayerNorm.weight', 'encoder.layer.11.attention.self.query.bias', 'encoder.layer.11.intermediate.dense.weight', 'encoder.layer.1.output.LayerNorm.bias', 'encoder.layer.4.output.LayerNorm.weight', 'classifier.weight', 'encoder.layer.8.output.dense.bias', 'encoder.layer.9.attention.self.key.bias', 'encoder.layer.5.attention.self.key.bias', '

In [22]:
def accuracy_thresh(y_pred, y_true, thresh=0.5, sigmoid=True):
    y_pred = torch.from_numpy(y_pred)
    y_true = torch.from_numpy(y_true)
    if sigmoid:
      y_pred = y_pred.sigmoid()
    return ((y_pred>thresh)==y_true.bool()).float().mean().item()

In [23]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    return {'accuracy_thresh': accuracy_thresh(predictions, labels)}

In [24]:
class MultilabelTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False):
        labels = inputs.pop("labels")
        outputs = model(**inputs)
        logits = outputs.logits
        loss_fct = torch.nn.BCEWithLogitsLoss()
        loss = loss_fct(logits.view(-1, self.model.config.num_labels),
                        labels.float().view(-1, self.model.config.num_labels))
        return (loss, outputs) if return_outputs else loss

In [32]:
batch_size = 8

args = TrainingArguments(
    output_dir="aift-model-review-multiple-label-classification",
    evaluation_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=10,
    weight_decay=0.01,
    use_cpu = False
)

In [33]:
model = AutoModelForSequenceClassification.from_pretrained(model_ckpt, num_labels=num_labels).to('cuda')

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [34]:
trainer = MultilabelTrainer(
    model,
    args,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    compute_metrics=compute_metrics,
    tokenizer=tokenizer)

In [35]:
trainer.evaluate()

{'eval_loss': 0.7062913179397583,
 'eval_accuracy_thresh': 0.4561224579811096,
 'eval_runtime': 0.2818,
 'eval_samples_per_second': 496.847,
 'eval_steps_per_second': 63.88}

In [36]:
trainer.train()

Checkpoint destination directory aift-model-review-multiple-label-classification/checkpoint-500 already exists and is non-empty.Saving will proceed but saved results may be invalid.


TrainOutput(global_step=700, training_loss=0.22303315843854632, metrics={'train_runtime': 47.1667, 'train_samples_per_second': 117.88, 'train_steps_per_second': 14.841, 'total_flos': 55632988457664.0, 'train_loss': 0.22303315843854632, 'epoch': 10.0})

In [104]:
saved_model_local_path = "./models"
# !mkdir ./aift-model-review-multiple-label-classification/models

mkdir: cannot create directory ‘./models’: File exists


In [39]:
trainer.save_model(saved_model_local_path)

In [69]:
history = trainer.evaluate()

In [70]:
history

{'eval_loss': 0.1798214465379715,
 'eval_accuracy_thresh': 0.9346938729286194,
 'eval_runtime': 0.2965,
 'eval_samples_per_second': 472.249,
 'eval_steps_per_second': 60.718,
 'epoch': 10.0}

In [110]:
from huggingface_hub import notebook_login

notebook_login()

## Predict

In [41]:
def predict(text,threshold):
    encoding = tokenizer(text, return_tensors="pt")
    encoding = {k: v.to(trainer.model.device) for k,v in encoding.items()}

    outputs = trainer.model(**encoding)
    logits = outputs.logits
    logits.shape
    # apply sigmoid + threshold
    sigmoid = torch.nn.Sigmoid()
    probs = sigmoid(logits.squeeze().cpu())
    predictions = np.zeros(probs.shape)
    print(predictions)
    print(probs)
    predictions[np.where(probs >= threshold)] = 1
    # turn predicted id's into actual label names
    predicted_labels = [id2label[idx] for idx, label in enumerate(predictions) if label == 1.0]
    print(predicted_labels)

In [57]:
text = "a lot of ads"
predict(text,0.4)

[0. 0. 0. 0. 0. 0. 0.]
tensor([0.9740, 0.0251, 0.1409, 0.7609, 0.0359, 0.0374, 0.0321],
       grad_fn=<SigmoidBackward0>)
['ads', 'negative']


In [60]:
label_text = id2label
model_name_or_path=model_ckpt
saved_model_path = saved_model_local_path


def predict_(input_text, saved_model_path,threshold):
    # initialize tokenizer
    tokenizer = AutoTokenizer.from_pretrained(model_name_or_path, use_fast=True)

    # preprocess and encode input text
    tokenizer_args = (input_text,)
    predict_input = tokenizer(
        *tokenizer_args,
        padding="max_length",
        max_length=128,
        truncation=True,
        return_tensors="pt",
    )

    # load trained model
    loaded_model = AutoModelForSequenceClassification.from_pretrained(saved_model_path)

    # get predictions
    output = loaded_model(predict_input["input_ids"])

    # return labels
    logits = output.logits
    logits.shape
    # apply sigmoid + threshold
    sigmoid = torch.nn.Sigmoid()
    probs = sigmoid(logits.squeeze().cpu())
    predictions = np.zeros(probs.shape)
    print(predictions)
    print(probs)
    predictions[np.where(probs >= threshold)] = 1
    # turn predicted id's into actual label names
    predicted_labels = [id2label[idx] for idx, label in enumerate(predictions) if label == 1.0]
    print(predicted_labels)

In [62]:
text='ew a lot of ads'
predict_(text, saved_model_path,0.4)

[0. 0. 0. 0. 0. 0. 0.]
tensor([0.5107, 0.1010, 0.5961, 0.2481, 0.2118, 0.1907, 0.1010],
       grad_fn=<SigmoidBackward0>)
['ads', 'positive']


# Custom training

In [99]:
PRE_BUILT_TRAINING_CONTAINER_IMAGE_URI = (
    "us-docker.pkg.dev/vertex-ai/training/pytorch-gpu.1-7:latest"
)

PYTHON_PACKAGE_APPLICATION_DIR = "python_package"

source_package_file_name = f"pipeline/aift-model-review-multiple-label-classification/{PYTHON_PACKAGE_APPLICATION_DIR}/dist/trainer-0.1.tar.gz"
python_package_gcs_uri = (
    f"{BUCKET_NAME}/pytorch-on-gcp/{APP_NAME}/train/python_package/trainer-0.1.tar.gz"
)
python_module_name = "trainer.task"

In [100]:
# !mkdir ./python_package

In [108]:
%%writefile ./aift-model-review-multiple-label-classification/{PYTHON_PACKAGE_APPLICATION_DIR}/setup.py

from setuptools import find_packages
from setuptools import setup
import setuptools

from distutils.command.build import build as _build
import subprocess


REQUIRED_PACKAGES = [
    'transformers',
    'datasets',
    'tqdm',
    'cloudml-hypertune'
]

setup(
    name='trainer',
    version='0.1',
    install_requires=REQUIRED_PACKAGES,
    packages=find_packages(),
    include_package_data=True,
    description='Vertex AI | Training | PyTorch | Text Classification | Python Package'
)

Overwriting ./aift-model-review-multiple-label-classification/python_package/setup.py


In [109]:
!cd aift-model-review-multiple-label-classification/{PYTHON_PACKAGE_APPLICATION_DIR} && python3 setup.py sdist --formats=gztar

running sdist
running egg_info
creating trainer.egg-info
writing trainer.egg-info/PKG-INFO
writing dependency_links to trainer.egg-info/dependency_links.txt
writing requirements to trainer.egg-info/requires.txt
writing top-level names to trainer.egg-info/top_level.txt
writing manifest file 'trainer.egg-info/SOURCES.txt'
reading manifest file 'trainer.egg-info/SOURCES.txt'
writing manifest file 'trainer.egg-info/SOURCES.txt'
running check
creating trainer-0.1
creating trainer-0.1/trainer
creating trainer-0.1/trainer.egg-info
copying files to trainer-0.1...
copying README.md -> trainer-0.1
copying setup.py -> trainer-0.1
copying trainer/__init__.py -> trainer-0.1/trainer
copying trainer/experiment.py -> trainer-0.1/trainer
copying trainer/metadata.py -> trainer-0.1/trainer
copying trainer/model.py -> trainer-0.1/trainer
copying trainer/task.py -> trainer-0.1/trainer
copying trainer/utils.py -> trainer-0.1/trainer
copying trainer.egg-info/PKG-INFO -> trainer-0.1/trainer.egg-info
copying t

In [82]:
!gsutil cp {source_package_file_name} {python_package_gcs_uri}

Copying file://python_package/dist/trainer-0.1.tar.gz [Content-Type=application/x-tar]...
/ [1 files][  916.0 B/  916.0 B]                                                
Operation completed over 1 objects/916.0 B.                                      


In [83]:
!gsutil ls -l {python_package_gcs_uri}

       916  2024-01-08T07:48:19Z  gs://ikame-gem-ai-research-bucket-review/pytorch-on-gcp/aift-review-classificatio-multiple-label/train/python_package/trainer-0.1.tar.gz
TOTAL: 1 objects, 916 bytes (916 B)


In [85]:
# !cd {PYTHON_PACKAGE_APPLICATION_DIR} && python -m trainer.task

In [86]:
aiplatform.init(project=PROJECT_ID, staging_bucket=BUCKET_NAME)

In [87]:
print(f"APP_NAME={APP_NAME}")
print(
    f"PRE_BUILT_TRAINING_CONTAINER_IMAGE_URI={PRE_BUILT_TRAINING_CONTAINER_IMAGE_URI}"
)
print(f"python_package_gcs_uri={python_package_gcs_uri}")
print(f"python_module_name={python_module_name}")

APP_NAME=aift-review-classificatio-multiple-label
PRE_BUILT_TRAINING_CONTAINER_IMAGE_URI=us-docker.pkg.dev/vertex-ai/training/pytorch-gpu.1-7:latest
python_package_gcs_uri=gs://ikame-gem-ai-research-bucket-review/pytorch-on-gcp/aift-review-classificatio-multiple-label/train/python_package/trainer-0.1.tar.gz
python_module_name=trainer.task


In [88]:
JOB_NAME = f"{APP_NAME}-pytorch-pkg-ar-{get_timestamp()}"
print(f"JOB_NAME={JOB_NAME}")

JOB_NAME=aift-review-classificatio-multiple-label-pytorch-pkg-ar-20240108075109


In [89]:
job = aiplatform.CustomPythonPackageTrainingJob(
    display_name=f"{JOB_NAME}",
    python_package_gcs_uri=python_package_gcs_uri,
    python_module_name=python_module_name,
    container_uri=PRE_BUILT_TRAINING_CONTAINER_IMAGE_URI,
)

In [90]:
training_args = ["--num-epochs", "2", "--model-name", "finetuned-bert-classifier"]

model = job.run(
    replica_count=1,
    machine_type="n1-standard-8",
    accelerator_type="NVIDIA_TESLA_V100",
    accelerator_count=1,
    args=training_args,
    sync=False,
)

Training Output directory:
gs://ikame-gem-ai-research-bucket-review/aiplatform-custom-training-2024-01-08-07:51:20.301 


INFO:google.cloud.aiplatform.training_jobs:Training Output directory:
gs://ikame-gem-ai-research-bucket-review/aiplatform-custom-training-2024-01-08-07:51:20.301 


View Training:
https://console.cloud.google.com/ai/platform/locations/us-central1/training/2282426366479564800?project=763889829809


INFO:google.cloud.aiplatform.training_jobs:View Training:
https://console.cloud.google.com/ai/platform/locations/us-central1/training/2282426366479564800?project=763889829809


CustomPythonPackageTrainingJob projects/763889829809/locations/us-central1/trainingPipelines/2282426366479564800 current state:
PipelineState.PIPELINE_STATE_RUNNING


...

INFO:google.cloud.aiplatform.training_jobs:CustomPythonPackageTrainingJob projects/763889829809/locations/us-central1/trainingPipelines/2282426366479564800 current state:
PipelineState.PIPELINE_STATE_RUNNING


CustomPythonPackageTrainingJob projects/763889829809/locations/us-central1/trainingPipelines/2282426366479564800 current state:
PipelineState.PIPELINE_STATE_RUNNING


INFO:google.cloud.aiplatform.training_jobs:CustomPythonPackageTrainingJob projects/763889829809/locations/us-central1/trainingPipelines/2282426366479564800 current state:
PipelineState.PIPELINE_STATE_RUNNING


CustomPythonPackageTrainingJob projects/763889829809/locations/us-central1/trainingPipelines/2282426366479564800 current state:
PipelineState.PIPELINE_STATE_RUNNING


INFO:google.cloud.aiplatform.training_jobs:CustomPythonPackageTrainingJob projects/763889829809/locations/us-central1/trainingPipelines/2282426366479564800 current state:
PipelineState.PIPELINE_STATE_RUNNING
